In [3]:
import pandas as pd
import numpy as np
from datetime import datetime
import os.path
import requests
import json

# Data cleaning

## Processing `paper_references.csv`
Null values in the DOI column are represented as different strings, so we remove all values that do not look like a DOI (do not start witn "10.")

In [17]:
papers_df = pd.read_csv("raw-paper_references.csv")

In [18]:
papers_df['DOI'].replace('^(?!10).*', '', regex=True, inplace=True)
papers_df.head(30)

ID  valid  No_de_Ref  new_ref  \
0    1      1          1        1   
1    2      1          2        2   
2    3      1          3        3   
3    4      1          4        4   
4    5      1          5        5   
5    6      1          6        6   
6    7      1          7        7   
7    8      1          8        8   
8    9      1          9        9   
9   10      1         10       10   
10  11      1         11       11   
11  12      1         12       12   
12  13      1         13       13   
13  14      1         14       14   
14  15      1         15       15   
15  16      1         16       16   
16  17      1         17       17   
17  18      1         18       18   
18  19      1         19       19   
19  20      1         20       20   
20  21      1         21       21   
21  22      1         22       22   
22  23      1         23       23   
23  24      1         24       24   
24  25      1         25       25   
25  26      1         26       26   
26  27      1         27       27   
27  28      1         28       28   
28  29      1         29       29   
29  30      1         30       30   

                                             filename  \
0                       1-s2.0-S092633731000086X-main   
1                        10.1016@j.cattod.2009.07.067   
2                       1-s2.0-S0926860X05006125-main   
3   27362718_Photo_reduction_of_CO2_to_methanol_vi...   
4                             10.1023@A@1011403320301   
5                       10.1016@S0360-5442(98)00070-X   
6                        10.1016@j.cattod.2009.07.081   
7                          10.1016@j.jcis.2010.12.034   
8                        10.1016@j.solmat.2007.06.003   
9                           10.1007@s10563-009-9065-9   
10                                   10.1039@B400326H   
11                                  10.1021@ja910091z   
12                       10.1016@j.carbon.2006.11.028   
13                                  10.1021@ja101318k   
14                                  10.1021@ja200804h   
15                   10.1016@j.cattod.2010.08.026.pdf   
16                          10.1007@s11244-007-9022-7   
17                                 10.1039@C0EE00780C   
18                                  10.1021@ja108791u   
19                        10.1016@S1872-20671060199-4   
20                       10.1016@j.fuproc.2010.09.007   
21                      10.1016@j.jclepro.2009.02.016   
22                                  10.1021@jz9000032   
23                       10.1016@j.apcatb.2009.01.010   
24                          10.1007@s11244-006-0100-z   
25                       10.1016@j.apcatb.2010.08.015   
26                      10.1016@S1010-6030(99)00113-6   
27  Kinetic_study_of_photocatalytic_reduction_of_C...   
28                          10.2478@v10026-010-0022-1   
29                       10.1016@j.catcom.2008.04.004   

                              DOI  \
0    10.1016/j.apcatb.2010.02.030   
1    10.1016/j.cattod.2009.07.067   
2    10.1016/j.apcata.2005.08.021   
3       10.1155/S1110662X05000176   
4         10.1023/A:1011403320301   
5   10.1016/S0360-5442(98)00070-X   
6    10.1016/j.cattod.2009.07.081   
7      10.1016/j.jcis.2010.12.034   
8    10.1016/j.solmat.2007.06.003   
9       10.1007/s10563-009-9065-9   
10               10.1039/B400326H   
11              10.1021/ja910091z   
12   10.1016/j.carbon.2006.11.028   
13              10.1021/ja101318k   
14              10.1021/ja200804h   
15   10.1016/j.cattod.2010.08.026   
16      10.1007/s11244-007-9022-7   
17             10.1039/C0EE00780C   
18              10.1021/ja108791u   
19  10.1016/S1872-2067(10)60199-4   
20   10.1016/j.fuproc.2010.09.007   
21  10.1016/j.jclepro.2009.02.016   
22              10.1021/jz9000032   
23   10.1016/j.apcatb.2009.01.010   
24      10.1007/s11244-006-0100-z   
25   10.1016/j.apcatb.2010.08.015   
26  10.1016/S1010-6030(99)00113-6   
27                                  
28      10.2478

### Export

In [19]:
papers_df.to_csv("paper_references.csv", index=False, sep=",")

## OpenAlex papers

### Taking list of DOIs

In [ ]:
papers_df = pd.read_csv("data/paper_references_curated.csv", sep=';')

Manual corrections in erroneous DOIs in `paper_references_curated.csv`
- 10.22146/ijc.841 --> 10.22146/ijc.21248
- paper con doi (incorrecto) 10.1007/s11244-017-0797 is repeated, the correct DOI is 10.1007/s11244-017-0797-x (appears in a previous row)
- 10.6084/m9.figshare.12715484 --> 10.1038/s41467-020-18350-7
- 10.1002/anie.x0xx00000x --> 10.1002/ange.202012019
- 10.1007/s10562-020-03426 --> 10.1007/s10562-020-03426-2
- 10.1002/slct.20200 --> 10.1002/slct.202004839

Papers without DOI:
- Kinetic study of photocatalytic reduction of CO2 over TiO2 --> https://openalex.org/W1629652031
- A study on the photoreduction of green house CO2 gas catalized by TiO2 to form methane an methanol --> not in OpenAlex
- Selective ethanol synthesis from carbon dioxide --> 10.1595/003214097x414166170
- Selective photoreduction of CO2HCO3 - to formate by aqueous suspensions and colloids of Pd-TiO2 --> 10.1021/j100372a080
 


### Downloading individual JSON files per paper from the DOI

In [ ]:
headers = {'Accept': 'application/json'}
query ='https://api.openalex.org/works/https://doi.org/{}'

#for doi in papers_df['DOI']:
for index, row in papers_df.iterrows():
    response = requests.get(query.format(row['DOI']), headers=headers)
    
    if response.status_code == 200:
        res_json = response.json()
        res_json['solar_id'] = row['No_de_Ref']
        with open('data/jsonOA/'+str(row['No_de_Ref'])+'.json', 'w') as file:
            file.write(json.dumps(res_json, indent=4))
    else:
        print(f"Error with {row['DOI']}, id {str(row['No_de_Ref'])}")
    


Error with nan, id 28
Error with nan, id 145
Error with 10.1007/s11244-017-0797, id 519


### Merging individual JSONs into one single file

In [ ]:
path = 'data/jsonOA/'
json_file_names = os.listdir(path)
json_file_names.remove('.DS_Store')

In [ ]:
merged_json = []
for file in json_file_names:
    filename = path + file
    with open(filename, 'r') as infile:
        merged_json.append(json.load(infile))
    
with open('data/papersOA.json', 'w') as out_json:
    json.dump(merged_json, out_json)

## Processing `catalystdata.csv`

In [4]:
exp_df = pd.read_csv("raw-catalystsdata.csv")

### Cleaning null values
Negative numbers and values that serve as null

In [5]:
exp_df.replace([-1,"-1", 0.0, 9999.99], '', inplace=True)
exp_df.head(30)

ID  No_de_Ref Catalyst_name TiO2_crystal_structure Catalyst Support  \
0    1          1          TiO2                Anatase     TiO2     NaN   
1    2          1          TiO2                Anatase     TiO2     NaN   
2    3          1       Ag/TiO2                Anatase     TiO2     NaN   
3    4          1       Ag/TiO2                Anatase     TiO2     NaN   
4    5          1       Ag/TiO2                Anatase     TiO2     NaN   
5    6          2          TiO2                    NaN     TiO2     NaN   
6    7          2          TiO2                    NaN     TiO2     NaN   
7    8          3       Cu/TiO2                Anatase     TiO2     NaN   
8    9          4          TiO2                Anatase     TiO2     NaN   
9   10          4       Cu/TiO2                Anatase     TiO2     NaN   
10  11          4       Cu/TiO2                Anatase     TiO2     NaN   
11  12          4       Cu/TiO2                Anatase     TiO2     NaN   
12  13          5          ZrO2                    NaN     ZrO2     NaN   
13  14          5          ZrO2                    NaN     ZrO2     NaN   
14  15          5          ZrO2                    NaN     ZrO2     NaN   
15  16          5          ZrO2                    NaN     ZrO2     NaN   
16  17          5          ZrO2                    NaN     ZrO2     NaN   
17  18          5          ZrO2                    NaN     ZrO2     NaN   
18  19          5          ZrO2                    NaN     ZrO2     NaN   
19  20          6          TiO2                Anatase     TiO2     NaN   
20  21          7       Pt/TiO2                    P25     TiO2     NaN   
21  22          7       Pt/TiO2                    P25     TiO2     NaN   
22  23          8          TiO2                Anatase     TiO2     NaN   
23  24          8      CuO/TiO2                Anatase     TiO2     NaN   
24  25          9          TiO2                    P25     TiO2     NaN   
25  26          9          TiO2                    P25     TiO2     NaN   
26  27          9          TiO2                    P25     TiO2     NaN   
27  28          9          ZrO2                    NaN     ZrO2     NaN   
28  29          9          ZrO2                    NaN     ZrO2     NaN   
29  30          9          ZrO2                    NaN     ZrO2     NaN   

   support_percent Co_catalyst co_catalyst_2 co_catalyst_3  ... C4H10_mol_m2h  \
0                          NaN           NaN           NaN  ...                 
1                           Ag           NaN           NaN  ...                 
2                           Ag           NaN           NaN  ...                 
3                           Ag           NaN           NaN  ...                 
4                           Ag           NaN           NaN  ...                 
5                          NaN           NaN           NaN  ...                 
6                          NaN           NaN           NaN  ...                 
7                           Cu           NaN           NaN  ...                 
8                          NaN           NaN           NaN  ...                 
9                           Cu           NaN           NaN  ...                 
10                          Cu           NaN           NaN  ...                 
11                          Cu           NaN           NaN  ...                 
12                         NaN           NaN           NaN  ...                 
13                         NaN           NaN           NaN  ...                 
14                         NaN           NaN           NaN  ...                 
15                         NaN           NaN           NaN  ...                 
16                         NaN           NaN           NaN  ...                 
17                         NaN           NaN           NaN  ...                 
18                         NaN           NaN           NaN  ...                 
19                         NaN           NaN           NaN

### Cleaning values in field `Masscat_g`
Some values are float (g), others have different measurements corresponding to different concepts or even comments. Filtering out all that do not correspond to grams.

In [9]:
def clean_masscat(masscat):
    try:
        masscat = float(masscat)
        return(masscat)
    
    except ValueError or TypeError:
        return('')
    

exp_df.Masscat_g = exp_df.Masscat_g.apply(clean_masscat)
exp_df.Masscat_g

0        0.1
1        0.1
2        0.1
3        0.1
4        0.1
        ... 
6659     0.1
6660    0.02
6661    0.02
6662    0.02
6663    0.02
Name: Masscat_g, Length: 6664, dtype: object

### Aligning values with ontology hierarchies

#### Reactor types

In [19]:
exp_df.Reactor_type.replace(('\s', 'Batch'), '', regex=True, inplace=True)
exp_df.Reactor_type.unique()

array(['Slurry', 'Fixed-bed', 'OpticalFiber', 'Monolithic', 'Membrane',
       'Fluidised-bed', ''], dtype=object)

#### Light Sources

In [11]:
## incompleto, mitad de jerarquía con obi: y la otra con solar:
exp_df.Light_source.replace('\s', '', regex=True, inplace=True)
exp_df.Light_source.unique()

array(['UV', 'Solar', 'Visible', 'UV-Vis', 'SolarSimulator',
       'Monochromatic', 'Vis'], dtype=object)

#### Lamps

In [15]:
exp_df.Lamp.replace({"Mercury(Hg)":"Mercury", 
                              "Xenon(Xe)":"Xenon", 
                              "Solar":"SolarSimulator",  
                              "Not spedified":"", 
                              "Mercury-Xenon(Hg-Xe)":"Mercury-Xenon", 
                              "Tungsten(W)":"Tungsten"}, inplace=True)
exp_df.Lamp.unique()

array(['Mercury', 'Fluorescent', 'Xenon', 'SolarSimulator', 'Halogen', '',
       'Tungsten-Halide', 'Mercury-Xenon', 'Other', 'LED', 'Tungsten',
       nan], dtype=object)

#### Wavelengths

In [13]:
def set_wavelengths(wl):
    try:
        wl = float(wl)
        if (wl) >= 192 and (wl) <= 280:
            return("192-280")
        elif (wl) >= 280 and (wl) <= 315:
            return("280-315")
        elif (wl) >= 315 and (wl) <= 400:
            return("315-400")
        elif (wl) >= 400 and (wl) <= 780:
            return("400-780")
        elif (wl) >= 315 and (wl) <= 780:
            return("315-780")
        elif (wl) >= 280 and (wl) <= 780:
            return("280-780")
        elif (wl) >= 192 and (wl) <= 780:
            return("192-780")
        
    except ValueError:
        wl = wl.replace('192-280(UV-A)', '192-280')
        wl = wl.replace('315-400(UV-C)', '315-400')
        wl = wl.replace('280-315(UV-B)', '280-315')
        return(wl)
    
    except TypeError:
        return('')
    

exp_df.Wavelength_nm = exp_df.Wavelength_nm.apply(set_wavelengths)
exp_df.Wavelength_nm.unique()    


array(['192-280', '315-400', '280-315', '400-780', None, '315-780',
       '192-780', '280-780', ''], dtype=object)

### Export

In [20]:
exp_df.to_csv("catalystsdata.csv", index=False, sep=",")